# Data Gathering

In [1]:
%matplotlib widget

In [99]:
from utils.io import gen_id_dated, gdf_viewer, gdf_geom, gdf_merger, na_col_drop, na_line_drop
import re, os
import numpy as np
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point
import datetime as dtm
import matplotlib.pyplot as plt
from definitions import ROOT_DIR

In [3]:
def gdf_filter(data, position=True,id_col='ID', bypass_col=[], dist_crit=2, rapp_val=2, verbose=False):
    """
    filter a dataframe of duplicate values (considering ID and/or position)
    """
    
    drop_idx = []
    check_idx = []
    id_list = []
    cols = data.columns.to_list()

    for i in range(len(data)):
        uid = data.loc[i,id_col]
        tmp = data[data[id_col]== f"{uid}"]
        
        if position: # use position XY
            pos_1 = Point(data.loc[i,'X'], data.loc[i,'Y'])

            if uid not in id_list and len(tmp) >=2:
                id_list.append(uid)

                for j in tmp.index: # retrieve duplicates ID index
                    if j != i:
                        pos_2 = Point(data.loc[j, 'X'], data.loc[j, 'Y'])
                        dist = pos_1.distance(pos_2)
                        
                        """if re.search('int|float', gdf[i + '_x'].dtype.name):
                            med = np.mean([gdf[i + '_x'].median(skipna=True), gdf[i + '_y'].median(skipna=True)])
                            xgap = abs(gdf.loc[j, i + '_x'] - med) # gap between the value and median
                            ygap = abs(gdf.loc[j, i + '_y'] - med)
                        """

                        if dist <= dist_crit:
                            start = data.columns.to_list().index('Y')+1
                            if j not in drop_idx:
                                for c in range(start, len(data.columns)):
                                    if cols[c] not in bypass_col:
                                        # print('1-', cols[c])
                                        if data.iloc[i,c] == data.iloc[j,c]: # all values (str, numeric)
                                            same = True

                                        elif data.iloc[i,c] != data.iloc[j,c] and re.search('int|float', data[cols[c]].dtype.name):
                                            """
                                            if xgap < ygap:
                                                gdf.loc[j, i] = gdf.loc[j, i + '_x']
                                                gdf.loc[j, i + '_x'] = np.nan
                                                gdf.loc[j, i + '_y'] = np.nan
                                            else:
                                                gdf.loc[j, i] = gdf.loc[j, i + '_y']
                                                gdf.loc[j, i + '_x'] = np.nan
                                                gdf.loc[j, i + '_y'] = np.nan
                                            """
                                            
                                            rapp = max(data.iloc[i,c], data.iloc[j,c])/min(data.iloc[i,c], data.iloc[j,c])
                                            if rapp <= rapp_val:
                                                same = True
                                            else:
                                                same = False
                                                if j not in check_idx: check_idx.append(j)
                                                if verbose: print(f"check [{j},{cols[c]}]")
                                        else : # str values
                                            same = False
                                            if j not in check_idx: check_idx.append(j)
                                            if verbose: print(f"check [{j},{cols[c]}]")
                                        
                                if same: drop_idx.append(j) # same objet -> most be dropped
                                    
        else: # without position XY, use ID
            if uid not in id_list and len(tmp) >=2:
                id_list.append(uid)

                for j in tmp.index:
                    if j != i:
                        start = data.columns.to_list().index('Y')+1
                        if j not in drop_idx:
                            for c in range(start, len(data.columns)):
                                if cols[c] not in bypass_col:
                                    # print('2-',cols[c])
                                    if data.iloc[i,c] == data.iloc[j,c]:
                                        same = True

                                    elif data.iloc[i,c] != data.iloc[j,c] and re.search('int|float', data[cols[c]].dtype.name):
                                        rapp = max(data.iloc[i,c], data.iloc[j,c])/min(data.iloc[i,c], data.iloc[j,c])
                                        if rapp <= rapp_val:
                                            same = True
                                        else:
                                            same = False
                                            if j not in check_idx: check_idx.append(j)
                                            if verbose: print(f"check [{j},{cols[c]}]")
                                    else :
                                        same = False
                                        if j not in check_idx: check_idx.append(j)
                                        if verbose: print(f"check [{j},{cols[c]}]")

                            if same: drop_idx.append(j) # same objet -> most be dropped
        
            
    check_data = data.loc[check_idx, :]
    if len(check_data) >0:
        print(f"some data must be checked , look at indices : {check_idx}")
        
    data.drop(index=drop_idx, inplace=True)
    data.reset_index(drop=True,inplace=True)
    print(f"Rows : {data.shape[0]} ; Columns : {data.shape[1]} ; Unique on '{id_col}' : {len(set(data[id_col]))} ; ")
    
    return data, check_data

In [4]:
def files_search(work_dir, files_dict, prefix='', skip=None, details=False):   
    
    if skip is None:
        skip = "we don't want to skip a word"
        
    for k in files_dict.keys():
        tmp_list = []
        for p,d,f in os.walk(work_dir):
            for x in f:
                add = False
                if re.search(prefix,x,re.I) and not re.search(skip,x,re.I):
                    add = True
                    i = str(f'{p}/{x}')
                else:
                    add = False
                    i=''
                    
                if re.search(k,i,re.I) and add:
                    tmp_list.append(i)
        files_dict.update({k:tmp_list})

    for k,v in files_dict.items():
        print(k,' \t: ',len(v))
    
    if details: # Look filenames
        which = files_dict.keys()

        for w in which:
            print('\n+++++++++++++++++')
            print(f'+  {w.upper()}\t+ ')
            print('+++++++++++++++++')
            [print(i, '-', x) for i, x in enumerate(files_dict[w], 0)]    


In [5]:
def check_col(data):
    cols_idx = []
    
    class DoubledColumns(Exception):
        """Merging process doubled column(s) still remain. Check and drop them before continue"""
        pass
    
    for i in range(len(data.columns)):
        if re.search('_x|_y', list(data.columns)[i]):
            cols_idx.append(i)
    
    if len(cols_idx) != 0 :
        raise DoubledColumns(f'Merging process doubled column(s) still remain.'
                             f'\nCheck and drop them before continue ! Doubled columns position {cols_idx}')

## Files reading

In [6]:
work_dir=ROOT_DIR+'/CF_data/Result_traitem/'

In [7]:
# create my dictionary structure to retrieve good files (Keynames !!!)
files_dict={'Borehole':0,'Piezometer':0,'Litho':0, 'Trench':0,'Equipm':0,
        'Measure':0,'Sample':0,'Analysis':0,'facility':0}

In [8]:
files_search(work_dir, files_dict, prefix='', skip='source')

Borehole  	:  5
Piezometer  	:  14
Litho  	:  6
Trench  	:  1
Equipm  	:  2
Measure  	:  6
Sample  	:  26
Analysis  	:  20
facility  	:  4


In [9]:
files_dict['Borehole']

['/home/yanathan/Projects/GSDMA/CF_data/Result_traitem/Prof_contact_sol_forage/Feuil1_Boreholes.csv',
 '/home/yanathan/Projects/GSDMA/CF_data/Result_traitem/Forage_Pilote/leve_Z_elect_pos_Boreholes.csv',
 '/home/yanathan/Projects/GSDMA/CF_data/Result_traitem/database_Memoris3/Profils_sol_Boreholes.csv',
 '/home/yanathan/Projects/GSDMA/CF_data/Result_traitem/donnees_terrain_2019/Donnees_forage_Boreholes.csv',
 '/home/yanathan/Projects/GSDMA/CF_data/Result_traitem/profils_sols_donnees_forages/donnees_forage_Boreholes.csv']

In [10]:
how=['inner', 'outer', 'left', 'right']

In [11]:
f = False # not plot df with gdf_view (only stats)
t = True

# Boreholes

Some corrections todo in 'data organization':
- correct extraction in the file 2 -> Samples
- file 4 and file 5 are the same in result (check it)
- try to concatenate file 1 with piezo (if possible because no position)
- check processing for 'refus and 'type_refus' (every object)

In [12]:
key='Borehole'
coi=['ID','ID_date','X','Y','Z','Type','Long_for','Diam_for','Refus'] #columns of interest
print(len(files_dict[key]), 'files')

5 files


In [13]:
df1 = pd.read_csv(files_dict[key][0], delimiter=',')
df2 = pd.read_csv(files_dict[key][3], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

#gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - Position data
df2 - Position data
Rows : 8, columns : 6, Unique on 'ID': 8


interactive(children=(IntSlider(value=3, description='rows', max=8, min=3, readout=False), IntSlider(value=6, …

Rows : 16, columns : 18, Unique on 'ID': 16


interactive(children=(IntSlider(value=3, description='rows', max=16, min=3, readout=False), IntSlider(value=12…

(None, None)

In [14]:
df2.ID=df2.ID.apply(lambda x: 'F'+x)

In [15]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf) # check if columns with '..._x' or '..._y' are still present and raise an error


Columns dropped :['Long_for_x', 'X_x', 'Y_x', 'Z_x', 'Type_x', 'X_y', 'Y_y', 'Z_y', 'Type_y', 'Long_for_y', 'Diam_ext_pz', 'Diam_int_pz', 'Long_pz', 'Crep_long']



/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

In [16]:
gdf_viewer(mdf, rows=3, un_val='ID', view=t)

Rows : 17, columns : 14, Unique on 'ID': 17


interactive(children=(IntSlider(value=3, description='rows', max=17, min=3, readout=False), IntSlider(value=12…

In [17]:
boreholes = mdf.copy() #saving

In [18]:
df1 = pd.read_csv(files_dict[key][2], delimiter=',')
df2 = pd.read_csv(files_dict[key][4], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

#gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - No position data
df2 - Position data
Rows : 826, columns : 6, Unique on 'ID': 172


interactive(children=(IntSlider(value=3, description='rows', max=826, min=3, readout=False), IntSlider(value=6…

Rows : 13, columns : 13, Unique on 'ID': 13


interactive(children=(IntSlider(value=3, description='rows', max=13, min=3, readout=False), IntSlider(value=12…

(None, None)

In [19]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf)


Columns dropped :['ID_date_x', 'Date_ouv_x', 'Type_x', 'Societe_x', 'Method_x', 'ID_date_y', 'Date_ouv_y', 'Method_y', 'Societe_y', 'Type_y']



In [20]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=f)

Rows : 839, columns : 13, Unique on 'ID': 185


#### Last merging

In [21]:
boreholes, err_df=gdf_merger(boreholes, mdf, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(boreholes)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

...

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['X_x', 'Y_x', 'Z_x', 'Diam_for_x', 'Refus_x', 'Type_refus_x', 'Type_x', 'Long_for_x', 'X_y', 'Y_y', 'Z_y', 'Long_for_y', 'Diam_for_y', 'Refus_y', 'Type_refus_y', 'Type_y']

1 NaN lines dropped

Columns dropped :['Refus_y', 'Type_refus_x', 'Type_refus_y']



/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/pandas/core/frame.py:4305: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


DoubledColumns: Merging process doubled column(s) still remain.
Check and drop them before continue ! Doubled columns position [4, 5, 7, 10, 11, 12]

In [22]:
boreholes.columns[[4, 5, 7, 9, 11, 12]]

Index(['ID_date_x', 'Date_ouv_x', 'Societe_x', 'Method', 'ID_date_y',
       'Societe_y'],
      dtype='object')

In [23]:
gdf_viewer(boreholes, rows=3, un_val='ID', view=t)

Rows : 852, columns : 21, Unique on 'ID': 198


interactive(children=(IntSlider(value=3, description='rows', max=852, min=3, readout=False), IntSlider(value=1…

In [24]:
err_df

ID  Date_ouv_x  Date_ouv_y     ID_date_x   ID_date_y  \
0        F205  2019-10-07  2010-03-26      2019-205   2010-F205   
1        F205  2019-10-07  2010-03-26      2019-205   2010-F205   
2        F212  2019-10-07  2010-05-10      2019-212   2010-F212   
3        F212  2019-10-07  2010-05-10      2019-212   2010-F212   
4        F212  2019-10-07  2010-05-10      2019-212   2010-F212   
..        ...         ...         ...           ...         ...   
830     F612b         NaN  2010-08-03           NaN  2010-F612b   
831      F221  2019-10-07         NaN      2019-221         NaN   
832  F224 bis  2019-10-08         NaN  2019-224 bis         NaN   
833      F220  2019-10-08         NaN      2019-220         NaN   
834  F220 bis  2019-10-08         NaN  2019-220 bis         NaN   

            Societe_x          Societe_y  
0    ECOPLANNING sprl            SITEREM  
1    ECOPLANNING sprl            SITEREM  
2    ECOPLANNING sprl            SITEREM  
3    ECOPLANNING sprl            SITEREM  
4    ECOPLANNING sprl            SITEREM  
..                ...                ...  
830               NaN  SBS Environnement  
831  ECOPLANNING sprl                NaN  
832  ECOPLANNING sprl                NaN  
833  ECOPLANNING sprl                NaN  
834  ECOPLANNING sprl                NaN  

[835 rows x 7 columns]

# Piezometers

Some corrections todo in 'data organization':
- file 0 and file 1 are the same in result (check it)
- file 6 doesn't have 'Type' column
- file 14 contains 'Equipment' data
- files 15 and 16 are the same
- file 17 contains 'Z' but no need 

In [25]:
key='Piezometer'
coi=['ID','ID_date','X','Y','Z','Type','Long_for','Diam_for','Refus'] #columns of interest
print(len(files_dict[key]), 'files')

14 files


In [26]:
df1 = pd.read_csv(files_dict[key][0], delimiter=',')
df2 = pd.read_csv(files_dict[key][2], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

#gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - Position data
df2 - Position data
Rows : 30, columns : 9, Unique on 'ID': 30


interactive(children=(IntSlider(value=3, description='rows', max=30, min=3, readout=False), IntSlider(value=9,…

Rows : 59, columns : 7, Unique on 'ID': 32


interactive(children=(IntSlider(value=3, description='rows', max=59, min=3, readout=False), IntSlider(value=7,…

(None, None)

In [27]:
df2, check = gdf_filter(df2, position=True, id_col='ID', bypass_col=['Refus'], dist_crit=2, rapp_val=2)
#gdf_viewer(df2, rows=5, un_val='ID', view=f)

Rows : 32 ; Columns : 7 ; Unique on 'ID' : 32 ; 


In [28]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf)


Columns dropped :['X_x', 'Y_x', 'Long_for_x', 'X_y', 'Y_y', 'Long_for_y']



/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

In [29]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=f)

Rows : 55, columns : 12, Unique on 'ID': 55


In [30]:
piezometers = mdf.copy() #saving

In [31]:
df1 = pd.read_csv(files_dict[key][1], delimiter=',')
df2 = pd.read_csv(files_dict[key][3], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

#gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - Position data
df2 - Position data
Rows : 29, columns : 7, Unique on 'ID': 29


interactive(children=(IntSlider(value=3, description='rows', max=29, min=3, readout=False), IntSlider(value=7,…

Rows : 14, columns : 10, Unique on 'ID': 14


interactive(children=(IntSlider(value=3, description='rows', max=14, min=3, readout=False), IntSlider(value=10…

(None, None)

In [32]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf)


Columns dropped :['X_x', 'Y_x', 'Long_for_x', 'Type_x', 'X_y', 'Y_y', 'Long_for_y', 'Type_y']



/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

In [33]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=f)

Rows : 33, columns : 12, Unique on 'ID': 33


In [34]:
piezometers, err_df=gdf_merger(piezometers, mdf, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(piezometers)
gdf_viewer(piezometers, rows=3, cols=13, un_val='ID', view=f)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['X_x', 'Y_x', 'Z_x', 'Zsol_x', 'Long_pz_sol_x', 'Equip_top_x', 'Equip_base_x', 'Type_equip_x', 'Type_x', 'Long_for_x', 'X_y', 'Y_y', 'Z_y', 'Zsol_y', 'Long_pz_sol_y', 'Equip_top_y', 'Equip_base_y', 'Type_equip_y', 'Type_y', 'Long_for_y']


Columns dropped :['Type_equip_y']

Rows : 61, columns : 13, Unique on 'ID': 61


In [35]:
df1 = pd.read_csv(files_dict[key][6], delimiter=',')
df2 = pd.read_csv(files_dict[key][5], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

#gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - Position data
df2 - Position data
Rows : 117, columns : 13, Unique on 'ID': 117


interactive(children=(IntSlider(value=3, description='rows', max=117, min=3, readout=False), IntSlider(value=1…

Rows : 6, columns : 6, Unique on 'ID': 6


interactive(children=(IntSlider(value=3, description='rows', max=6, min=3, readout=False), IntSlider(value=6, …

(None, None)

In [36]:
df1, check = gdf_filter(df1, position=True, id_col='ID', bypass_col=['Refus'], dist_crit=2, rapp_val=2)
gdf_viewer(df2, un_val='ID', view=f)

Rows : 117 ; Columns : 13 ; Unique on 'ID' : 117 ; 
Rows : 6, columns : 6, Unique on 'ID': 6


In [37]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['X_x', 'Y_x', 'Zsol_x', 'Type_x', 'X_y', 'Y_y', 'Zsol_y', 'Ht_Chbre', 'Type_y']



/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

In [38]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=f)

Rows : 123, columns : 13, Unique on 'ID': 123


In [39]:
piezometers, err_df=gdf_merger(piezometers, mdf, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(piezometers)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['X_x', 'Y_x', 'Z_x', 'Zsol_x', 'Long_pz_x', 'Type_x', 'X_y', 'Y_y', 'Z_y', 'Zsol_y', 'Long_pz_y', 'Type_y']

21 NaN lines dropped

Columns dropped :['ID', 'Type_x', 'Type_y']



/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/pandas/core/frame.py:4305: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


In [40]:
gdf_viewer(piezometers, rows=3, cols=13, un_val='ID', view=f)

Rows : 183, columns : 19, Unique on 'ID': 183


In [41]:
df1 = pd.read_csv(files_dict[key][8], delimiter=',')
df2 = pd.read_csv(files_dict[key][9], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

#gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - Position data
df2 - Position data
Rows : 117, columns : 13, Unique on 'ID': 117


interactive(children=(IntSlider(value=3, description='rows', max=117, min=3, readout=False), IntSlider(value=1…

Rows : 10, columns : 9, Unique on 'ID': 10


interactive(children=(IntSlider(value=3, description='rows', max=10, min=3, readout=False), IntSlider(value=9,…

(None, None)

In [42]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['X_x', 'Y_x', 'Zsol_x', 'Type_x', 'X_y', 'Y_y', 'Zsol_y', 'Type_y']



In [43]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=f)

Rows : 127, columns : 17, Unique on 'ID': 127


In [44]:
piezometers, err_df=gdf_merger(piezometers, mdf, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals(), debug=False)
check_col(piezometers)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['X_x', 'Y_x', 'Z_x', 'Zsol_x', 'Long_pz_sol_x', 'Long_for_x', 'Equip_base_x', 'Equip_top_x', 'Societe_x', 'Terrain_x', 'Long_crep_x', 'Diam_int_pz_x', 'Zone_x', 'Sous_zone_x', 'Type_x', 'Long_pz_x', 'X_y', 'Y_y', 'Z_y', 'Zsol_y', 'Societe_y', 'Zone_y', 'Sous_zone_y', 'Long_pz_y', 'Long_crep_y', 'Diam_int_pz_y', 'Terrain_y', 'Long_for_y', 'Long_pz_sol_y', 'Equip_top_y', 'Equip_base_y', 'Type_y']

21 NaN lines dropped

Columns dropped :['Sous_zone_x', 'Sous_zone_y']



/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/pandas/core/frame.py:4305: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


In [45]:
gdf_viewer(piezometers, rows=3, cols=13, un_val='ID', view=f)

Rows : 183, columns : 19, Unique on 'ID': 183


In [46]:
df1 = pd.read_csv(files_dict[key][10], delimiter=',')
df2 = pd.read_csv(files_dict[key][11], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

#gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - Position data
df2 - Position data
Rows : 257, columns : 6, Unique on 'ID': 254


interactive(children=(IntSlider(value=3, description='rows', max=257, min=3, readout=False), IntSlider(value=6…

Rows : 3, columns : 18, Unique on 'ID': 3


interactive(children=(IntSlider(value=3, description='rows', max=3, min=3, readout=False), IntSlider(value=12,…

(None, None)

In [47]:
df2['ID'] = df2['ID'].astype('object')

In [48]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['Z', 'X_x', 'Y_x', 'Type_x', 'X_y', 'Y_y', 'Type_y', 'Refus', 'Type_refus']



In [49]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=f)

Rows : 260, columns : 17, Unique on 'ID': 257


In [50]:
piezometers, err_df=gdf_merger(piezometers, mdf, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())#, debug=True)
check_col(piezometers)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

...

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)



Columns dropped :['X_x', 'Y_x', 'Type_x', 'Long_pz_x', 'Long_for_x', 'Societe_x', 'Diam_int_pz_x', 'X_y', 'Y_y', 'Long_for_y', 'Diam_int_pz_y', 'Long_pz_y', 'Societe_y', 'Type_y']

20 NaN lines dropped


/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/pandas/core/frame.py:4305: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


DoubledColumns: Merging process doubled column(s) still remain.
Check and drop them before continue ! Doubled columns position [9, 14]

In [54]:
data = piezometers.copy()
for i in data.index:
    x = data.loc[i, 'Terrain_x']
    y = data.loc[i, 'Terrain_y']
    
    if not isinstance(x, float):
        x = str(x[:3]).lower()
    if not isinstance(y, float):
        y = str(y[:3]).lower()
        
    if x == y:
        if x == 'all': 
            data.loc[i, 'Terrain'] = 'Alluvions'
        elif x == 'rem':
            data.loc[i, 'Terrain'] = 'Remblais'
data.drop(columns=['Terrain_x', 'Terrain_y'], inplace=True)
piezometers = data.copy()

In [56]:
data = piezometers.copy()
for i in data.index:
    x = data.loc[i, 'Terrain']
    
    if not pd.isnull(x):
        x = str(x[:3]).lower()
        
    if x == 'all': 
        data.loc[i, 'Terrain'] = 'Alluvions'
    elif x == 'rem':
        data.loc[i, 'Terrain'] = 'Remblais'
piezometers = data.copy()

In [58]:
gdf_viewer(piezometers, rows=3, cols=13, un_val='ID', view=t)

Rows : 406, columns : 27, Unique on 'ID': 403


interactive(children=(IntSlider(value=3, description='rows', max=406, min=3, readout=False), IntSlider(value=1…

In [59]:
df1 = pd.read_csv(files_dict[key][12], delimiter=',')
df2 = pd.read_csv(files_dict[key][13], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

#gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - Position data
df2 - No position data
Rows : 12, columns : 18, Unique on 'ID': 12


interactive(children=(IntSlider(value=3, description='rows', max=12, min=3, readout=False), IntSlider(value=12…

Rows : 11, columns : 8, Unique on 'ID': 11


interactive(children=(IntSlider(value=3, description='rows', max=11, min=3, readout=False), IntSlider(value=8,…

(None, None)

In [60]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf)


Columns dropped :['Z_x', 'Long_pz_x', 'Type_x', 'Z_y', 'Type_y', 'Long_pz_y']



In [61]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=t)

Rows : 12, columns : 22, Unique on 'ID': 12


interactive(children=(IntSlider(value=3, description='rows', max=12, min=3, readout=False), IntSlider(value=13…

In [62]:
# temporary save to come back as 'ctrl-Z'
tmp_save = piezometers.copy()
piezometers = tmp_save.copy()

#### Last merging

In [64]:
piezometers, err_df=gdf_merger(piezometers, mdf, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(piezometers)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['X_x', 'Y_x', 'Z_x', 'Refus_x', 'Long_crep_x', 'ID_date_x', 'Date_ouv_x', 'Diam_for_x', 'Diam_ext_pz_x', 'Type_x', 'Long_pz_x', 'Long_for_x', 'Terrain_x', 'Societe_x', 'Diam_int_pz_x', 'ID_date_y', 'X_y', 'Y_y', 'Z_y', 'Date_ouv_y', 'Long_for_y', 'Diam_for_y', 'Diam_ext_pz_y', 'Diam_int_pz_y', 'Long_crep_y', 'Societe_y', 'Refus_y', 'Terrain_y', 'Type_y', 'Long_pz_y']

20 NaN lines dropped


/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/pandas/core/frame.py:4305: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


In [66]:
data = piezometers.copy()
for i in data.index:
    x = data.loc[i, 'Terrain']
    
    if not pd.isnull(x):
        x = str(x[:3]).lower()
        
    if x == 'all': 
        data.loc[i, 'Terrain'] = 'Alluvions'
    elif x == 'rem':
        data.loc[i, 'Terrain'] = 'Remblais'
        
piezometers = data.copy()

In [67]:
gdf_viewer(piezometers, rows=3, cols=13, un_val='ID', view=t)

Rows : 418, columns : 33, Unique on 'ID': 415


interactive(children=(IntSlider(value=3, description='rows', max=418, min=3, readout=False), IntSlider(value=1…

There are some special duplicates (different ID but same position)

- piezometers.query("ID=='P2' or ID=='P2M'")

###### Checking

# Equipments

In [69]:
key='Equipm'
coi=['ID','ID_date','X','Y','Z','Type','Long_for','Diam_for','Refus'] #columns of interest
print(len(files_dict[key]), 'files')

2 files


In [70]:
df1 = pd.read_csv(files_dict[key][0], delimiter=',')
df2 = pd.read_csv(files_dict[key][1], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

#gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - No position data
df2 - No position data
Rows : 33, columns : 6, Unique on 'ID': 9


interactive(children=(IntSlider(value=3, description='rows', max=33, min=3, readout=False), IntSlider(value=6,…

Rows : 36, columns : 6, Unique on 'ID': 12


interactive(children=(IntSlider(value=3, description='rows', max=36, min=3, readout=False), IntSlider(value=6,…

(None, None)

In [71]:
df1['ID'] = df1['ID'].astype('object')

In [72]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['Equip_top_x', 'Equip_base_x', 'Diam_for_x', 'Legende_x', 'Equip_top_y', 'Equip_base_y', 'Diam_for_y', 'Legende_y']



In [73]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=t)

Rows : 69, columns : 7, Unique on 'ID': 21


interactive(children=(IntSlider(value=3, description='rows', max=69, min=3, readout=False), IntSlider(value=7,…

In [74]:
equipments = mdf

# Lithologies

Some corrections todo in 'data organization':

In [75]:
key='Litho'
coi=['ID','X','Y','Z','Litho_top','Litho_base','Description'] #columns of interest
print(len(files_dict[key]), 'files')

6 files


In [76]:
df1 = pd.read_csv(files_dict[key][0], delimiter=',')
df2 = pd.read_csv(files_dict[key][1], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')

gdf_view = True
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - Position data
df2 - Position data
Rows : 51, columns : 7, Unique on 'ID': 29


interactive(children=(IntSlider(value=3, description='rows', max=51, min=3, readout=False), IntSlider(value=7,…

Rows : 109, columns : 7, Unique on 'ID': 71


interactive(children=(IntSlider(value=3, description='rows', max=109, min=3, readout=False), IntSlider(value=7…

(None, None)

In [77]:
df1['Litho_base'] = df1['Litho_base'].apply(lambda v : re.sub(',','.',v) if not pd.isnull(v) else v)
df1['Litho_base'] = df1['Litho_base'].astype('float')

In [78]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
check_col(mdf)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['X_x', 'Y_x', 'Z_x', 'Litho_top_x', 'Litho_base_x', 'X_y', 'Y_y', 'Z_y', 'Litho_top_y', 'Litho_base_y']

Ambiguous values in both columns compared, change it manually !
Columns ['ID', 'Terrain_x', 'Terrain_y'] must be dropped manually !
error file created in 'tmp_files/merging_error_log(df1-df2).csv'


/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

DoubledColumns: Merging process doubled column(s) still remain.
Check and drop them before continue ! Doubled columns position [4, 5]

In [79]:
data = mdf.copy()
col = 'Terrain'

id_list = []
keep_idx = []

for i in data.index:
    _id = data.loc[i,'ID']
    if re.search("'", _id): 
        _id = f"`{_id}`" # it doesn't work 
    else:
        _id = f"{_id}"
    
    if _id not in id_list:
        id_list.append(_id)
        tmp = data[data['ID']==f"{_id}"]

        if len(tmp) < 2 and len(tmp) > 0:
            keep_idx = keep_idx + list(tmp.index)
        else:
            tmp = tmp[tmp[col]==tmp[col]]
            keep_idx = keep_idx + list(tmp.index)
print(keep_idx)
    
data = data.loc[keep_idx,:]
data.drop(columns=[col+'_x', col+'_y'], inplace=True)
data.reset_index(drop=True, inplace=True)

[0, 3, 4, 5, 6, 7, 11, 15, 16, 19, 20, 21, 24, 25, 28, 29, 32, 33, 36, 37, 40, 41, 44, 45, 46, 49, 50, 51, 52, 55, 56, 59, 60, 63, 64, 67, 68, 71, 72, 73, 76, 77, 80, 81, 84, 85, 88, 89, 92, 93, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154]


In [80]:
mdf = data.copy()

In [81]:
gdf_viewer(mdf, rows=10, cols=13, un_val='ID', view=t)

Rows : 108, columns : 7, Unique on 'ID': 70


interactive(children=(IntSlider(value=10, description='rows', max=108, min=10, readout=False), IntSlider(value…

In [82]:
lithologies = mdf.copy()

In [83]:
df1 = pd.read_csv(files_dict[key][2], delimiter=',')
df2 = pd.read_csv(files_dict[key][3], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')
    
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - Position data
df2 - No position data
Rows : 1423, columns : 14, Unique on 'ID': 330


interactive(children=(IntSlider(value=3, description='rows', max=1423, min=3, readout=False), IntSlider(value=…

Rows : 1629, columns : 9, Unique on 'ID': 299


interactive(children=(IntSlider(value=3, description='rows', max=1629, min=3, readout=False), IntSlider(value=…

(None, None)

In [84]:
df1.drop(columns=['Societe','Description'], inplace=True)

In [85]:
df1['X'] = df1['X'].apply(lambda v : re.sub(',','.',v) if not pd.isnull(v) else v)
df1['Y'] = df1['Y'].apply(lambda v : re.sub(',','.',v) if not pd.isnull(v) else v)
df1['Ep_remb'] = df1['Ep_remb'].apply(lambda v : re.sub(',','.',v) if not pd.isnull(v) else v)

In [86]:
df1['Type'] = df1['Type'].astype('object')
df1[['X','Y','Ep_remb']] = df1[['X','Y','Ep_remb']].astype('float')

In [87]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=f)


Columns dropped :['Type_x', 'Type_y']

Rows : 7511, columns : 19, Unique on 'ID': 405


In [88]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=t)

Rows : 7511, columns : 19, Unique on 'ID': 405


interactive(children=(IntSlider(value=3, description='rows', max=7511, min=3, readout=False), IntSlider(value=…

In [89]:
# temporary save to come back as 'ctrl-Z'
#tmp_save = lithologies.copy()
lithologies = tmp_save.copy()

In [90]:
lithologies, err_df=gdf_merger(lithologies, mdf, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals(), debug=t)
check_col(lithologies)

column: X_x
X 0
X 1
X 2
X 3
X 4
X 5
X 6
X 7
X 8
X 9
X 10
X 11
X 12
X 13
X 14
X 15
X 16
X 17
X 18
X 19
X 20
X 21
X 22
X 23
X 24
X 25
X 26
X 27
X 28
X 29
X 30
X 31
X 32
X 33
X 34
X 35
X 36
X 37
X 38
X 39
X 40
X 41
X 42
X 43
X 44
X 45
X 46
X 47
X 48
X 49
X 50
X 51
X 52
X 53
X 54
X 55
X 56
X 57
X 58
X 59
X 60
X 61
X 62
X 63
X 64
X 65
X 66
X 67
X 68
X 69
X 70
X 71
X 72
X 73
X 74
X 75
X 76
X 77
X 78
X 79
X 80
X 81
X 82
X 83
X 84
X 85
X 86
X 87
X 88
X 89
X 90
X 91
X 92
X 93
X 94
X 95
X 96
X 97
X 98
X 99
X 100
X 101
X 102
X 103
X 104
X 105
X 106
X 107
X 108
X 109
X 110
X 111
X 112
X 113
X 114
X 115
X 116
X 117
X 118
X 119
X 120
X 121
X 122
X 123
X 124
X 125
X 126
X 127
X 128
X 129
X 130
X 131
X 132
X 133
X 134
X 135
X 136
X 137
X 138
X 139
X 140
X 141
X 142
X 143
X 144
X 145
X 146
X 147
X 148
X 149
X 150
X 151
X 152
X 153
X 154
X 155
X 156
X 157
X 158
X 159
X 160
X 161
X 162
X 163
X 164
X 165
X 166
X 167
X 168
X 169
X 170
X 171
X 172
X 173
X 174
X 175
X 176
X 177
X 178
X 179
X 180
X 181
X 182


/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

X 963
X 964
X 965
X 966
X 967
X 968
X 969
X 970
X 971
X 972
X 973
X 974
X 975
X 976
X 977
X 978
X 979
X 980
X 981
X 982
X 983
X 984
X 985
X 986
X 987
X 988
X 989
X 990
X 991
X 992
X 993
X 994
X 995
X 996
X 997
X 998
X 999
X 1000
X 1001
X 1002
X 1003
X 1004
X 1005
X 1006
X 1007
X 1008
X 1009
X 1010
X 1011
X 1012
X 1013
X 1014
X 1015
X 1016
X 1017
X 1018
X 1019
X 1020
X 1021
X 1022
X 1023
X 1024
X 1025
X 1026
X 1027
X 1028
X 1029
X 1030
X 1031
X 1032
X 1033
X 1034
X 1035
X 1036
X 1037
X 1038
X 1039
X 1040
X 1041
X 1042
X 1043
X 1044
X 1045
X 1046
X 1047
X 1048
X 1049
X 1050
X 1051
X 1052
X 1053
X 1054
X 1055
X 1056
X 1057
X 1058
X 1059
X 1060
X 1061
X 1062
X 1063
X 1064
X 1065
X 1066
X 1067
X 1068
X 1069
X 1070
X 1071
X 1072
X 1073
X 1074
X 1075
X 1076
X 1077
X 1078
X 1079
X 1080
X 1081
X 1082
X 1083
X 1084
X 1085
X 1086
X 1087
X 1088
X 1089
X 1090
X 1091
X 1092


/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

X 1093
X 1094
X 1095
X 1096
X 1097
X 1098
X 1099
X 1100
X 1101
X 1102
X 1103
X 1104
X 1105
X 1106
X 1107
X 1108
X 1109
X 1110
X 1111
X 1112
X 1113
X 1114
X 1115
X 1116
X 1117
X 1118
X 1119
X 1120
X 1121
X 1122
X 1123
X 1124
X 1125
X 1126
X 1127
X 1128
X 1129
X 1130
X 1131
X 1132
X 1133
X 1134
X 1135
X 1136
X 1137
X 1138
X 1139
X 1140
X 1141
X 1142
X 1143
X 1144
X 1145
X 1146
X 1147
X 1148
X 1149
X 1150
X 1151
X 1152
X 1153
X 1154
X 1155
X 1156
X 1157
X 1158
X 1159
X 1160
X 1161
X 1162
X 1163
X 1164
X 1165
X 1166
X 1167
X 1168
X 1169
X 1170
X 1171
X 1172
X 1173
X 1174
X 1175
X 1176
X 1177
X 1178
X 1179
X 1180
X 1181
X 1182
X 1183
X 1184
X 1185
X 1186
X 1187
X 1188
X 1189
X 1190
X 1191
X 1192
X 1193
X 1194
X 1195
X 1196
X 1197
X 1198
X 1199
X 1200
X 1201
X 1202
X 1203
X 1204
X 1205
X 1206
X 1207
X 1208
X 1209
X 1210
X 1211
X 1212
X 1213
X 1214
X 1215
X 1216
X 1217
X 1218
X 1219
X 1220
X 1221
X 1222
X 1223
X 1224
X 1225
X 1226
X 1227
X 1228
X 1229
X 1230
X 1231
X 1232
X 1233
X 1234
X 1235

...

Z 7821
Z 7822
Z 7823
Z 7824
Z 7825
Z 7826
Z 7827
Z 7828
Z 7829
Z 7830
Z 7831
Z 7832
Z 7833
Z 7834
Z 7835
Z 7836
Z 7837
Z 7838
Z 7839
Z 7840
Z 7841
Z 7842
Z 7843
Z 7844
Z 7845
Z 7846
Z 7847
Z 7848
Z 7849
Z 7850
Z 7851
Z 7852
Z 7853
Z 7854
Z 7855
Z 7856
Z 7857
Z 7858
Z 7859
Z 7860
Z 7861
Z 7862
Z 7863
Z 7864
Z 7865
Z 7866
Z 7867
Z 7868
Z 7869
Z 7870
Z 7871
Z 7872
Z 7873
Z 7874
Z 7875
Z 7876
Z 7877
Z 7878
Z 7879
Z 7880
Z 7881
Z 7882
Z 7883
Z 7884
Z 7885
Z 7886
Z 7887
Z 7888
Z 7889
Z 7890
Z 7891
Z 7892
Z 7893
Z 7894
Z 7895
Z 7896
Z 7897
Z 7898
Z 7899
Z 7900
Z 7901
Z 7902
Z 7903
column: Sous_zone_x


/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme

column: Date_ouv_x
column: ID_date_x
column: Terrain_x
column: Societe_x
column: Zone_x
column: Refus_x

Columns dropped :['X_x', 'Y_x', 'Z_x', 'Refus_x', 'Sous_zone_x', 'Zone_x', 'ID_date_x', 'Date_ouv_x', 'Type_x', 'Societe_x', 'X_y', 'Y_y', 'Z_y', 'Refus_y', 'Zone_y', 'Sous_zone_y', 'ID_date_y', 'Date_ouv_y', 'Societe_y', 'Type_y']

20 NaN lines dropped


/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/pandas/core/frame.py:4305: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


DoubledColumns: Merging process doubled column(s) still remain.
Check and drop them before continue ! Doubled columns position [18, 21]

In [91]:
lithologies[lithologies.columns[[18,21]]]

Terrain_x Terrain_y
0          NaN       NaN
1          NaN       NaN
2          NaN       NaN
3          NaN       NaN
4          NaN       NaN
...        ...       ...
7899       NaN       NaN
7900       NaN       NaN
7901       NaN       NaN
7902       NaN       NaN
7903       NaN       NaN

[7904 rows x 2 columns]

In [92]:
df1 = pd.read_csv(files_dict[key][4], delimiter=',')
df2 = pd.read_csv(files_dict[key][5], delimiter=',')

if 'X' in list(df1.columns): print('df1 - Position data')
else: print('df1 - No position data')
if 'X' in list(df2.columns): print('df2 - Position data')
else: print('df2 - No position data')
    
gdf_viewer(df1, rows=3, un_val='ID', view=t), gdf_viewer(df2, rows=3, un_val='ID', view=t)

df1 - No position data
df2 - No position data
Rows : 91, columns : 7, Unique on 'ID': 25


interactive(children=(IntSlider(value=3, description='rows', max=91, min=3, readout=False), IntSlider(value=7,…

Rows : 54, columns : 5, Unique on 'ID': 24


interactive(children=(IntSlider(value=3, description='rows', max=54, min=3, readout=False), IntSlider(value=5,…

(None, None)

In [93]:
mdf, err_df=gdf_merger(df1, df2, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals())
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=f)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['Litho_top_x', 'Litho_base_x', 'Description_x', 'Keyword_x', 'Litho_top_y', 'Litho_base_y', 'Keyword_y', 'Description_y']

Rows : 145, columns : 7, Unique on 'ID': 49


In [94]:
gdf_viewer(mdf, rows=3, cols=13, un_val='ID', view=t)

Rows : 145, columns : 7, Unique on 'ID': 49


interactive(children=(IntSlider(value=3, description='rows', max=145, min=3, readout=False), IntSlider(value=7…

In [95]:
lithologies, err_df=gdf_merger(lithologies, mdf, how=how[1], col='ID', dist_max=2, non_na=1, scope=globals(), debug=False)
check_col(lithologies)

/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/home/yanathan/.local/share/virtualenvs/GSDMA-DRfwm83x/lib/python3.8/site-packages/numpy/lib/nanfunctions.py:1111: RuntimeWarning: Mean of empty slice
  return np.nanme


Columns dropped :['Description_x', 'Litho_top_x', 'Litho_base_x', 'Terrain', 'Description_y', 'Litho_base_y', 'Litho_top_y']

Ambiguous values in both columns compared, change it manually !
Columns ['ID', 'Type_x', 'Type_y', 'Terrain_x', 'Terrain_y', 'Zone_x', 'Zone_y'] must be dropped manually !
error file created in 'tmp_files/merging_error_log(lithologies-mdf).csv'


DoubledColumns: Merging process doubled column(s) still remain.
Check and drop them before continue ! Doubled columns position [18, 21, 25, 30, 32, 33]

In [111]:
gdf_viewer(lithologies[lithologies.columns[[18,21,25,30,32,33]]], rows=3)

IndexError: index 30 is out of bounds for axis 0 with size 26

In [110]:
gdf_viewer(lithologies, rows=3, cols=13, un_val='ID', view=t)

Rows : 8044, columns : 26, Unique on 'ID': 839


interactive(children=(IntSlider(value=3, description='rows', max=8044, min=3, readout=False), IntSlider(value=…

# Samples

Some corrections todo in 'data organization':
- file 0 and file 1 are the same in result (check it)

# Measures

Some corrections todo in 'data organization':
- file 0 and file 1 are the same in result (check it)

# Analysis

Some corrections todo in 'data organization':
- file 0 and file 1 are the same in result (check it)